# Digitizing the raw data

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import math
import pandas as pd
import os
from datetime import datetime
import time as lime

Specifiying paths for loading data set. Set colors and scan flags in the parameterList

In [2]:
Github_folder =R"C:\Users\Rohit Prasad Bhatt"
#Github_folder =R"C:\Users\Jan"
#Github_folder =R"C:\Users\Lilo"
#Github_folder= "/Users/fredjendrzejewski"

class scanparameter:
    def __init__(self, flag, path, color):
        self.flag = flag
        self.path  = os.path.join(Github_folder, "Documents/GitHub/sopa_rsi/analysis_data/Sodium_Accurate_Atom_Counting/Oct07_Scan_0000_Cam_EXPOT=0.2")
        self.color = color

ParameterList = [scanparameter("Cam_EXPOT=0.2", 1, '.-r')]
            #scanparameter("KtwoDInt=1.4", 1, '.-r'),
              #scanparameter("KtwoDInt=2.3", 1, '.-b'),
              #scanparameter("use_K=True", 1, '.-b'),
              #scanparameter("use_K=False", 1, '.-r')]
now = datetime.now()

set scan parameters

In [3]:
time_between_atom_images = 12e-3
Cam_EXPOT = 200e-3
one_atom_signal= 11530.41# 11593.8 #level for one signal
number_of_images_without_atoms = 100

function for digitizing the data

In [4]:
def digitizing (data, one_atom_signal, number_of_images_without_atoms, time_between_atom_images, Cam_EXPOT):
    'data is a 2d array whose rows are individual runs'
    'one atom signal is the expected jump step from histograms'
    digitized_data = data+0 #create a deepcopy 
    N= data.shape[0] #number of runs 
    atom_images = data.shape[1] #number of images in each run 
    time = np.arange(atom_images)*(time_between_atom_images+Cam_EXPOT)
    for i in range(N):
        # we set the weird jumps to zero
        data[i][0]=0
        data[i][100]=0
        data[i][101]=0
        
        #first digitization routine: 
        #Caculate offset from first half of the first reference set
        #Digitize data by removing offset and dividing and rounding the one_atom_signal
        offset=np.mean(data[i][0:int(number_of_images_without_atoms/2-1)])
        digitized_data[i][:]=np.round((data[i][:]-offset)/one_atom_signal,0)
        
        previous = None
        count = 1
        counts = np.array([])
        elements = np.array([])
        startingindex = np.array([])
        
        for image in range(len(digitized_data[i])-2):
            n=image+1        
            element = digitized_data[i][n]
            if element == previous :
                count += 1
            else :
                if previous != None:
                    counts = np.append(counts,np.array([count]),axis=0)
                    elements = np.append(elements,np.array([digitized_data[i][n-1]]),axis=0)
                    startingindex = np.append(startingindex,np.array([n]),axis=0)
                    if count <= 3:
                        for a in range(count):
                            digitized_data[i][n-count+a] = digitized_data[i][n-count-1]
                previous = element
                count = 1
    return digitized_data, time, atom_images
    

lets actually digitize the data

In [5]:
n = sum(1 for p in ParameterList)
for p in ParameterList:
    #savingpath = os.path.join(Dropbox_folder + Dropbox_path + now.strftime("\%Y-%m-%d") + scan + "_of_" + day.split("20",1)[1] + "_" + p.flag +'_digitized_on' + now.strftime("_%Y-%m-%d") +'.csv')
    #setattr(p, 'savepath', savingpath)
    #plottingpath = os.path.join(Dropbox_folder + Dropbox_path + now.strftime("\%Y-%m-%d") + "\\test" + scan + "_of_" + day.split("20",1)[1] + "_" + p.flag +'_digitized_on' + now.strftime("_%Y-%m-%d") +'.png')
    #plottingpath = os.path.join(Dropbox_folder + Dropbox_path + now.strftime("\%Y-%m-%d") + scan + "_of_" + day.split("20",1)[1] + "_" + p.flag +'_digitized_on' + now.strftime("_%Y-%m-%d") +'.pdf')
    #setattr(p, 'plotpath', plottingpath)
    #print(savingpath)
    #print(p.path)
    Counts = pd.read_csv(p.path+ '.csv',  encoding='UTF-8')
    N = len(Counts['Run_number'].unique())
    setattr(p, 'N', N)
    Split_Counts = np.array_split(Counts['Counts'],p.N)
    setattr(p, 'Counts', np.array(Split_Counts))
    
    
    Counts_digitized, time, atom_images = digitizing(p.Counts, one_atom_signal, number_of_images_without_atoms, time_between_atom_images, Cam_EXPOT)
    setattr(p, 'digitizedCounts', Counts_digitized)
    setattr(p, 'time', time)
    setattr(p, 'atom_images', atom_images)
    
    runnumbers = np.array([])
    for i in range(p.N):
        runnumbers = np.append(runnumbers,np.tile(np.array([i]),p.atom_images))
        setattr(p, 'runnumber',runnumbers)
    


In [6]:
for p in ParameterList:
    cols = 3
    rows = int(math.ceil(p.N/cols))
    fig1 = plt.figure(figsize=(25,800))
    #plt.title('S'+ scan.split("S",1)[1] + ' of ' + day.split("20",1)[1] + '   ' + p.flag, size=30)
    for n in range(p.N):
        ax = fig1.add_subplot(rows, cols, n+1)
        y = p.Counts[n]
        y2 = p.digitizedCounts[n]
        offset=np.mean(y[0:49])
        ax.set_ylim([-1,4])
        #ax.set_xlim([20,80])
        ax.plot(np.arange(y.size),y2, '.-k')
        ax.plot(np.arange(y.size),(y-offset)/one_atom_signal, p.color)
        ax.set_xlabel("Time [s]")
        ax.set_ylabel("Counts")
        ax.grid()
    fig1.tight_layout()
    fig1.subplots_adjust(top=0.9);
    
    #plt.savefig('graph'+str('{:.0f}'.format(lime.time()-1608118962))+'.pdf', format='pdf')

run next cell only if you want to save the data!

In [7]:
for p in ParameterList:
    savedata=pd.DataFrame({'Run_number':p.runnumber, 'Counts':p.digitizedCounts.flatten()})
    savedata.to_csv('digitized.csv', index=False)